In [1]:
# Import packages
library(rstan)
library(coda)
library(parallel)
library(Bessel)

Loading required package: StanHeaders
Loading required package: ggplot2
Registered S3 methods overwritten by 'ggplot2':
  method         from 
  [.quosures     rlang
  c.quosures     rlang
  print.quosures rlang
rstan (Version 2.19.2, GitRev: 2e1f913d3ca3)
For execution on a local, multicore CPU with excess RAM we recommend calling
options(mc.cores = parallel::detectCores()).
To avoid recompilation of unchanged Stan programs, we recommend calling
rstan_options(auto_write = TRUE)
For improved execution time, we recommend calling
Sys.setenv(LOCAL_CPPFLAGS = '-march=native')
although this causes Stan to throw an error on a few processors.

Attaching package: 'coda'

The following object is masked from 'package:rstan':

    traceplot



In [2]:
# add path required by rstan
library(devtools) 
Sys.setenv(PATH = paste("C:/Rtools/bin", Sys.getenv("PATH"), sep=";")) 
Sys.setenv(PATH = paste("C:\\Rtools\\mingw_64\\bin", Sys.getenv("PATH"), sep=";")) 
Sys.setenv(BINPREF = "C:/Rtools/mingw_$(WIN)/bin/")

Loading required package: usethis


# Read csv into dataframe

In [3]:
dat.str <- Sys.glob("data.*.csv")
data <- as.data.frame(read.csv(file = dat.str))
# slicing training set (whole 2018 season)
dat <- data[data$period < 29,]

In [4]:
head(dat)

X   Date       Season round period home.name away.name home.score
136 154 2018-04-25 2018   5     28     CW        ES        101       
137 155 2018-04-24 2018   5     28     ME        RI         56       
138 156 2018-04-22 2018   5     28     BL        GC         71       
139 157 2018-04-22 2018   5     28     NM        HW         98       
140 158 2018-04-21 2018   5     28     FR        WB        108       
141 159 2018-04-21 2018   5     28     PA        GE         50       
    away.score home.goals ... Total.Score.Over.Min Total.Score.Over.Max
136  52        14         ... 1.9                  1.9                 
137 102         8         ... 1.9                  1.9                 
138  76        10         ... 1.9                  1.9                 
139  70        14         ... 1.9                  1.9                 
140  54        16         ... 1.9                  1.9                 
141  84         7         ... 1.9                  1.9                 
    Total.Score.Over.Close Total.Score.Under.Open Total.Score.Under.Min
136 1.9                    1.9                    1.9                  
137 1.9                    1.9                    1.9                  
138 1.9                    1.9                    1.9                  
139 1.9                    1.9                    1.9                  
140 1.9                    1.9                    1.9                  
141 1.9                    1.9                    1.9                  
    Total.Score.Under.Max Total.Score.Under.Close Notes home.number away.number
136 1.9                   1.9                           10          16         
137 1.9                   1.9                           12          11         
138 1.9                   1.9                            9           6         
139 1.9                   1.9                           13          15         
140 1.9                   1.9                            7          14         
141 1.9                   1.9                            3           8

In [5]:
# library(hash)

# h <- hash()

# for (i in 1:length(sort(unique(dat$home.name)))){
#     h[[as.character(sort(unique(dat$home.name))[i])]] <- i
# }

In [82]:
# library(hash)

# h <- hash()

# for (i in 1:length(sort(unique(dat$home.name)))){
#     h[[as.character(sort(unique(dat$home.name))[i])]] <- i
# }

# home.number <- vector()
# away.number <- vector()

# for (i in 1:nrow(dat)){
#     home.number <- append(home.number, h[[as.character(dat$home.name[i])]])
#     away.number <- append(away.number, h[[as.character(dat$away.name[i])]])
    
# }

# dat$home.number <- home.number
# dat$away.number <- away.number

In [84]:
# write.csv(dat, 'temp.csv')

# 2019 Round 1 data

In [5]:
matchup <- data[data$period == 29,]
n.matches <- length(matchup$home.number)
matchup

X   Date       Season round period home.name away.name home.score
127 145 2018-04-29 2018   6     29     FR        WC         81       
128 146 2018-04-29 2018   6     29     CW        RI         70       
129 147 2018-04-29 2018   6     29     ES        ME         72       
130 148 2018-04-28 2018   6     29     AD        GC        110       
131 149 2018-04-28 2018   6     29     HW        SK         89       
132 150 2018-04-28 2018   6     29     GW        BL         77       
133 151 2018-04-28 2018   6     29     NM        PA         69       
134 152 2018-04-28 2018   6     29     GE        SY         69       
135 153 2018-04-27 2018   6     29     WB        CA         80       
    away.score home.goals ... Total.Score.Over.Min Total.Score.Over.Max
127  89        12         ... 1.9                  1.9                 
128 113        10         ... 1.9                  1.9                 
129 108        10         ... 1.9                  1.9                 
130  62        16         ... 1.9                  1.9                 
131  54        13         ... 1.9                  1.9                 
132  43        10         ... 1.9                  1.9                 
133 102        10         ... 1.9                  1.9                 
134  86        10         ... 1.9                  1.9                 
135  59        11         ... 1.9                  1.9                 
    Total.Score.Over.Close Total.Score.Under.Open Total.Score.Under.Min
127 1.9                    1.9                    1.9                  
128 1.9                    1.9                    1.9                  
129 1.9                    1.9                    1.9                  
130 1.9                    1.9                    1.9                  
131 1.9                    1.9                    1.9                  
132 1.9                    1.9                    1.9                  
133 1.9                    1.9                    1.9                  
134 1.9                    1.9                    1.9                  
135 1.9                    1.9                    1.9                  
    Total.Score.Under.Max Total.Score.Under.Close Notes home.number away.number
127 1.9                   1.9                            1           8         
128 1.9                   1.9                            5          12         
129 1.9                   1.9                           11          13         
130 1.9                   1.9                           17           7         
131 1.9                   1.9                           16          15         
132 1.9                   1.9                            6          10         
133 1.9                   1.9                           14           9         
134 1.9                   1.9                            4          18         
135 1.9                   1.9                            2           3

# Data

In [6]:
home.name <- as.matrix(dat$home.name)
away.name <- as.matrix(dat$away.name)
home.numb <- dat$home.number
away.numb <- dat$away.number

home.Goals <- dat$home.goals
home.Behinds <- dat$home.behinds
away.Goals <- dat$away.goals
away.Behinds <- dat$away.behinds

period <- dat$period
n.teams <- 18
n.games <- length(home.numb)
n.periods <- max(period)
n.bps <- 2
bps <- c(1,24)

In [7]:
# matricies for the Owen paper centering
ones <- matrix(1, nrow = (n.teams-1), ncol = 1)
S_t <-  n.teams / (n.teams-1) * (diag(n.teams-1) + ones %*% t(ones))

# Jmat is n * n-1
J.up.left <- diag(n.teams-1) - (1/n.teams)*(ones %*% t(ones))
J.bot.left <- - t(ones) * 1/n.teams

Jmat <- rbind(J.up.left, J.bot.left)

# Store data into list required by STAN

In [8]:
dat.list <- list(N = n.teams,
                 G = n.games,
                 T = n.periods,
                 period = period,
                 home = home.numb,
                 away = away.numb,
                 homeGoals = home.Goals,
                 homeBehinds = home.Behinds,
                 awayGoals = away.Goals,
                 awayBehinds = away.Behinds,
                 BP = n.bps,
                 Breaks = bps,
                 Smat = S_t,
                 JmatTrans = t(Jmat),
                 N_Matches = n.matches,
                 nextHome = matchup$home.number,
                 nextAway = matchup$away.number)

# Compile the model

In [9]:
prefit <- stan("Skellam goal and behind difference.stan", data = dat.list, chains = 0)

DIAGNOSTIC(S) FROM PARSER:
Info: Comments beginning with # are deprecated.  Please use // in place of # for line comments.
Info: assignment operator <- deprecated in the Stan language; use = instead.
Info: Comments beginning with # are deprecated.  Please use // in place of # for line comments.
Info: Comments beginning with # are deprecated.  Please use // in place of # for line comments.
Info: Comments beginning with # are deprecated.  Please use // in place of # for line comments.
Info: Comments beginning with # are deprecated.  Please use // in place of # for line comments.
Info: Comments beginning with # are deprecated.  Please use // in place of # for line comments.
Info: Comments beginning with # are deprecated.  Please use // in place of # for line comments.
Info: Comments beginning with # are deprecated.  Please use // in place of # for line comments.
Info: Comments beginning with # are deprecated.  Please use // in place of # for line comments.
Info: Comments beginning with # 

the number of chains is less than 1; sampling not done


# Sampling using MCMC (4 cores in parallel)

In [10]:
cl <- makeCluster(4)

clusterEvalQ(cl, library(rstan))

myfunction <- function(var1, var2, var3){
    stan(fit = var3, data = var2,
                            chains = 1, chain_id = var1, iter = 2500,
                            refresh = -1, init = "0")
}

sflist <- parLapply(cl, 1:4, fun = myfunction, var2 = dat.list, var3 = prefit)
stopCluster(cl)

[[1]]
 [1] "rstan"       "ggplot2"     "StanHeaders" "stats"       "graphics"   
 [6] "grDevices"   "utils"       "datasets"    "methods"     "base"       

[[2]]
 [1] "rstan"       "ggplot2"     "StanHeaders" "stats"       "graphics"   
 [6] "grDevices"   "utils"       "datasets"    "methods"     "base"       

[[3]]
 [1] "rstan"       "ggplot2"     "StanHeaders" "stats"       "graphics"   
 [6] "grDevices"   "utils"       "datasets"    "methods"     "base"       

[[4]]
 [1] "rstan"       "ggplot2"     "StanHeaders" "stats"       "graphics"   
 [6] "grDevices"   "utils"       "datasets"    "methods"     "base"

In [11]:
sflist

[[1]]
Inference for Stan model: Skellam goal and behind difference.
1 chains, each with iter=2500; warmup=1250; thin=1; 
post-warmup draws per chain=1250, total post-warmup draws=1250.

                           mean se_mean     sd   2.5%    25%    50%    75%
delta                      0.65    0.00   0.07   0.51   0.61   0.66   0.70
attackGoals_raw[1,1]       1.91    0.10   2.54  -3.27   0.21   2.10   3.70
attackGoals_raw[1,2]      -4.70    0.11   2.77  -8.87  -6.93  -5.00  -2.70
attackGoals_raw[1,3]      -3.54    0.12   3.32  -8.79  -6.17  -3.85  -1.09
attackGoals_raw[1,4]      -0.07    0.12   3.10  -6.24  -2.22  -0.04   2.04
attackGoals_raw[1,5]       0.51    0.11   2.64  -4.56  -1.24   0.44   2.21
attackGoals_raw[1,6]       1.01    0.10   2.79  -4.61  -0.93   1.11   2.93
attackGoals_raw[1,7]      -0.10    0.10   2.57  -5.12  -1.84  -0.10   1.54
attackGoals_raw[1,8]       1.38    0.13   2.66  -3.90  -0.50   1.42   3.27
attackGoals_raw[1,9]       1.37    0.06   1.92  -2.32   0.09   1

In [11]:
fit <- sflist2stanfit(sflist)

In [12]:
write.csv(print(summary(fit)), file = "fitproper.csv")

$summary
                                  mean      se_mean           sd          2.5%
delta                     9.202469e-01 0.0011880308 6.675619e-02  7.857552e-01
attackGoals_raw[1,1]      1.952346e+00 0.0795880116 2.682447e+00 -3.178661e+00
attackGoals_raw[1,2]     -1.515475e+00 0.0705043328 3.316372e+00 -7.883064e+00
attackGoals_raw[1,3]      1.478312e+00 0.0725590043 2.982298e+00 -4.349202e+00
attackGoals_raw[1,4]     -2.292941e+00 0.0724530233 2.870443e+00 -7.747947e+00
attackGoals_raw[1,5]      1.279209e+00 0.0669910772 3.164386e+00 -5.062099e+00
attackGoals_raw[1,6]      9.727132e-01 0.0703696204 2.949509e+00 -4.699909e+00
attackGoals_raw[1,7]      1.216037e+00 0.0677391995 2.926027e+00 -4.518857e+00
attackGoals_raw[1,8]     -1.028903e-01 0.0547448737 2.735204e+00 -5.520633e+00
attackGoals_raw[1,9]      9.796675e-03 0.0826821658 3.294277e+00 -6.515296e+00
attackGoals_raw[1,10]    -3.217648e+00 0.0612930121 3.305255e+00 -8.620776e+00
attackGoals_raw[1,11]     1.868619e+00 0.06

# Extract parameters

In [13]:
fit.samples <- extract(fit)
write.csv(fit.samples, file = "samples.csv")

# Take the average of the mu for each team

In [14]:
# parameter estimate extractor
delta <- mean (fit.samples$delta)
muAttGoals.vec <- apply(fit.samples$muAttGoals, 2, mean) # I think the 18th team here is
  # suffering from the sum to zero constraint, maybe will dissapear with more samples

muAttBehinds.vec <- apply(fit.samples$muAttBehinds, 2, mean)
muDef.vec <- apply(fit.samples$muDef, 2, mean)

mu.ests <- matrix(c( "Goal attack mean estimates", muAttGoals.vec,"Behind attack mean estimates", muAttBehinds.vec,
                     "defend means estimates", muDef.vec), ncol = 3, byrow = F)
write.csv(mu.ests, file = "AR mean estimates.csv")

# Extract phiAtt, phiDef, attackGoals, attackBehinds, defend

In [15]:
phiAtt.vec <- mean(fit.samples$phiAtt)
phiDef.vec <- mean(fit.samples$phiDef)
std.attack.vec <- mean(fit.samples$stdAtt)
std.def.vec <- mean(fit.samples$stdDef)

goal.attack.strenghts.mat <- apply(fit.samples$attackGoals, 2:3, mean)
write.csv(goal.attack.strenghts.mat, file = "goal.attack.str.csv")

behind.attack.strengths.mat <- apply(fit.samples$attackBehinds, 2:3, mean)
write.csv(behind.attack.strengths.mat, file = "behind.attack.str.csv")

defence.strengths.mat <- apply(fit.samples$defend, 2:3, mean)
write.csv(defence.strengths.mat, file = "def.str.csv")

par.vec <- c(delta, "delta",
             phiAtt.vec, "phi.attack",
             phiDef.vec, "phi.defend",
             std.attack.vec, "std.attack",
             std.def.vec, "std.defend")

par.vec.est <- matrix(par.vec, ncol = 2, byrow = T)
write.csv(par.vec.est,  file = "parameter estimates.csv")

# Extract goalDiff, behindDiff, and totalDiff

In [16]:
avg.pred.goal.diff <- apply(fit.samples$goalDiff, 2, mean)
avg.pred.behind.diff <- apply(fit.samples$behindDiff, 2, mean)
avg.pred.total.diff <- apply(fit.samples$totalDiff, 2, mean)

In [17]:
# see if we got it right
actual.total.diff <- matchup$home.score - matchup$away.score
correct.vec <- ((avg.pred.total.diff * actual.total.diff)>0)

In [18]:
actual.total.diff
correct.vec

[1]  -8 -43 -36  48  35  34 -33 -17  21

[1]  TRUE FALSE FALSE FALSE FALSE  TRUE FALSE FALSE  TRUE

# Calculate percentage of win, loss and draw

In [19]:
# get the percentage of win/loss

winDrawLossPer <- function(x.vec) {
  home.win.per <- mean(as.numeric(x.vec > 0))
  draw.per <- mean(as.numeric(x.vec == 0))
  away.win.per <- mean(as.numeric(x.vec < 0))
  c(home.win.per, draw.per ,away.win.per)
}

In [20]:
per.chance.mat <- apply(fit.samples$totalDiff, 2, winDrawLossPer)
per.chance.mat

iterations [,1]   [,2]   [,3]   [,4]   [,5]   [,6]   [,7]   [,8]   [,9]  
      [1,] 0.2322 0.9030 0.7130 0.0946 0.4640 0.7250 0.5954 0.7134 0.9232
      [2,] 0.0460 0.0108 0.0312 0.0078 0.0288 0.0612 0.0498 0.0272 0.0208
      [3,] 0.7218 0.0862 0.2558 0.8976 0.5072 0.2138 0.3548 0.2594 0.0560

In [21]:
# the sd ests are going to be wildly larger than they should due to not throwing out burn in
# samples, should probably change all my apply's to deal with this but ehhhhhhhh, more samples
# takes care of it for the most part
sd.ests <- round(apply(fit.samples$totalDiff,2,sd),2)

In [23]:
sim.pred.mat <- matrix(c("behind diff", avg.pred.behind.diff,
                         "goal diff", avg.pred.goal.diff,
                         "total diff", avg.pred.total.diff,
                         "home team", as.character(matchup$home.name),
                         "away team", as.character(matchup$away.name),
                         "actual result", actual.total.diff,
                         "prediction correct?", correct.vec,
                         "home win prob", per.chance.mat[1,],
                         "draw prob", per.chance.mat[2,],
                         "home loss prob", per.chance.mat[3,],
                         "simulated sd ests", sd.ests
                         ), nrow = 11, byrow = T)

write.csv(sim.pred.mat, file = "internal predictions.csv")

In [24]:
sim.pred.mat

[,1]                [,2]     [,3]    [,4]    [,5]     [,6]    [,7]   
 [1,] behind diff         1.1754   19.2424 0.211   -7.9574  2.9474  1.9496 
 [2,] goal diff           -3.009   4.1354  4.8136  -11.6542 -0.966  3.4572 
 [3,] total diff          -16.8786 44.0548 29.0926 -77.8826 -2.8486 22.6928
 [4,] home team           FR       CW      ES      AD       HW      GW     
 [5,] away team           WC       RI      ME      GC       SK      BL     
 [6,] actual result       -8       -43     -36     48       35      34     
 [7,] prediction correct? TRUE     FALSE   FALSE   FALSE    FALSE   TRUE   
 [8,] home win prob       0.2322   0.903   0.713   0.0946   0.464   0.725  
 [9,] draw prob           0.046    0.0108  0.0312  0.0078   0.0288  0.0612 
[10,] home loss prob      0.7218   0.0862  0.2558  0.8976   0.5072  0.2138 
[11,] simulated sd ests   33.66    61.88   70.94   116.14   49.18   50.34  
      [,8]   [,9]    [,10]  
 [1,] 2.2436 -1.0754 3.3494 
 [2,] 2.0994 4.5242  10.9066
 [3,] 14.84  26.0698 68.789 
 [4,] NM     GE      WB     
 [5,] PA     SY      CA     
 [6,] -33    -17     21     
 [7,] FALSE  FALSE   TRUE   
 [8,] 0.5954 0.7134  0.9232 
 [9,] 0.0498 0.0272  0.0208 
[10,] 0.3548 0.2594  0.056  
[11,] 51.99  61.99   93.61

In [25]:
write.csv(t(sim.pred.mat),  file = "round6_prediction.csv")